In [ ]:
!pip install playwright pandas openpyxl tqdm
!playwright install
!playwright install --with-deps chromium
!pip install nest_asyncio


Playwright Host validation warning: 
╔══════════════════════════════════════════════════════╗
║ Host system is missing dependencies to run browsers. ║
║ Missing libraries:                                   ║
║     libwoff2dec.so.1.0.2                             ║
║     libgstgl-1.0.so.0                                ║
║     libgstcodecparsers-1.0.so.0                      ║
║     libavif.so.13                                    ║
║     libharfbuzz-icu.so.0                             ║
║     libenchant-2.so.2                                ║
║     libsecret-1.so.0                                 ║
║     libhyphen.so.0                                   ║
║     libmanette-0.2.so.0                              ║
╚══════════════════════════════════════════════════════╝
    at validateDependenciesLinux (/usr/local/lib/python3.11/dist-packages/playwright/driver/package/lib/server/registry/dependencies.js:269:9)
    at process.processTicksAndRejections (node:internal/process/task_queues:105

In [ ]:
import nest_asyncio
nest_asyncio.apply()
import asyncio
from playwright.async_api import async_playwright, Page
import pandas as pd
from tqdm.asyncio import tqdm
from IPython.display import display
import re

**LƯU Ý: CHỈNH SỐ TRANG BẮT ĐẦU VÀ KẾT THÚC THEO PHÂN CÔNG Ở CELL CODE NGAY DƯỚI ĐÂY!**


Nhớ đổi cả output_file nha

In [ ]:
## CHỈNH SỬA Ở ĐÂY

# --- Cấu hình ---
BASE_URL = "https://careerviet.vn/viec-lam/tat-ca-viec-lam-vi.html"
# Cú pháp: "careerviet_jobs_full_details_{Số trang bắt đầu : Số trang kết thúc}.xlsx". Ví dụ "careerviet_jobs_full_details_1_84.xlsx"
OUTPUT_FILE = "careerviet_jobs_full_details_final.xlsx"


TRANG_BAT_DAU = 1 #CHỈNH SỐ TRANG BẮT ĐẦU THEO PHÂN CÔNG Ở ĐÂY  <==
TRANG_KET_THUC = 84 # CHỈNH SỐ TRANG KẾT THÚC THEO PHÂN CÔNG Ở ĐÂY  <==


# --- Các CSS/XPath Selector ---
JOB_ITEM_SELECTOR = "div.job-item"
JOB_TITLE_SELECTOR = "a.job_link"
COMPANY_NAME_SELECTOR = "div.caption a.company-name"
LOCATIONS_SELECTOR = "div.location ul li"
SALARY_SELECTOR = "div.salary p"
WELFARE_SELECTOR = "ul.welfare-list li"


In [ ]:


# --- Các hàm helper (Không đổi) ---
async def get_element_text(element, selector, default="N/A"):
    if not element: return default
    try:
        selected_element = await element.query_selector(selector)
        return (await selected_element.inner_text() if selected_element else default).strip()
    except Exception: return "N/A"

async def get_element_attribute(element, selector, attribute, default="N/A"):
    if not element: return default
    try:
        selected_element = await element.query_selector(selector)
        return (await selected_element.get_attribute(attribute) if selected_element else default)
    except Exception: return "N/A"

# --- Hàm cào danh sách công việc (Không đổi) ---
async def scrape_job_list_page(page: Page, page_num: int):
    if page_num <= 1:
        url = BASE_URL
    else:
        url = BASE_URL.replace('-vi.html', f'-trang-{page_num}-vi.html')

    print(f"Đang cào danh sách từ trang: {url}")
    try:
        await page.goto(url, wait_until="networkidle", timeout=90000)
        await page.wait_for_selector(JOB_ITEM_SELECTOR, timeout=70000)
    except Exception as e:
        print(f"Lỗi khi tải trang danh sách {url}: {e}")
        return []
    job_items = await page.query_selector_all(JOB_ITEM_SELECTOR)
    page_data = []
    print(f"Tìm thấy {len(job_items)} mục công việc trên trang {page_num}.")
    for item in job_items:
        job_title = await get_element_text(item, JOB_TITLE_SELECTOR)
        job_url_raw = await get_element_attribute(item, JOB_TITLE_SELECTOR, "href")
        job_url = f"https://careerviet.vn{job_url_raw}" if job_url_raw and not job_url_raw.startswith("http") else job_url_raw
        company_name = await get_element_text(item, COMPANY_NAME_SELECTOR)
        locations_elements = await item.query_selector_all(LOCATIONS_SELECTOR)
        locations = [(await loc.inner_text()).strip() for loc in locations_elements]
        location_str = ", ".join(filter(None, locations)) if locations else "N/A"
        salary_raw = await get_element_text(item, SALARY_SELECTOR)
        salary = salary_raw.split(":")[-1].strip() if ":" in salary_raw else (salary_raw if salary_raw else "N/A")
        page_data.append({
            "TieuDeCongViec": job_title, "TenCongTy": company_name, "DiaDiem": location_str,
            "MucLuong": salary, "URL": job_url,
        })
    return page_data

# --- Các hàm cào chi tiết từ trang con ---
async def extract_generic_section(page: Page, possible_titles: list[str]) -> str:
    print(f"INFO: Đang tìm các mục: {possible_titles}")
    try:
        vietnamese_lower = "abcdefghijklmnopqrstuvwxyzaaaaaaaaaaaaaaaaaadeeeeeeeeeeeiiiiiooooooooooooooooouuuuuuuuuuuuyyyyy"
        vietnamese_upper = "ABCDEFGHIJKLMNOPQRSTUVWXYZÁÀÃẢẠĂẮẰẴẲẶÂẤẦẪẨẬĐÉÈẼẺẸÊẾỀỄỂỆÍÌĨỈỊÓÒÕỎỌÔỐỒỖỔỘƠỚỜỠỞỢÚÙŨỦỤƯỨỪỮỬỰÝỲỸỶỴ"
        for title in possible_titles:
            title_xpath = (
                f"//*[self::h2 or self::h3 or self::strong]"
                f"[contains(translate(normalize-space(.), '{vietnamese_upper}', '{vietnamese_lower}'), '{title.lower()}')]"
            )
            title_element = await page.query_selector(title_xpath)
            if title_element:
                print(f"INFO: Tìm thấy tiêu đề khớp: '{title}'")
                container_xpath = "xpath=ancestor::div[contains(@class, 'detail-row')][1]"
                container = await title_element.query_selector(container_xpath)
                if container:
                    container_text = await container.inner_text()
                    title_text = await title_element.inner_text()
                    content_text = container_text.replace(title_text, '', 1).strip()
                    return ' '.join(content_text.split()) or "N/A"
                else:
                    print(f"CẢNH BÁO: Tìm thấy tiêu đề '{title}' nhưng không tìm thấy khối cha 'detail-row'.")
                    continue
        print(f"CẢNH BÁO: Không tìm thấy mục nào với các tiêu đề đã cho: {possible_titles}")
        return "N/A"
    except Exception as e:
        print(f"LỖI khi trích xuất mục chung: {e}")
        return "N/A"

async def extract_deadline(page: Page) -> str:
    print("INFO: Đang tìm và trích xuất mục: 'Hạn nộp'")
    try:
        selector_v1 = "//strong[contains(text(),'Hết hạn nộp')]/following-sibling::p"
        deadline_element = await page.query_selector(selector_v1)
        if not deadline_element:
            selector_v2 = "//td[.//text()[normalize-space()='Hết hạn nộp']]/following-sibling::td"
            deadline_element = await page.query_selector(selector_v2)
        if deadline_element: return (await deadline_element.inner_text()).strip()
        print("CẢNH BÁO: Không tìm thấy Hạn nộp với tất cả các cấu trúc đã biết.")
        return "N/A"
    except Exception as e:
        print(f"LỖI khi trích xuất Hạn nộp: {e}")
        return "N/A"

async def extract_welfare_benefits(page: Page) -> str:
    print("INFO: Đang tìm và trích xuất mục: 'Phúc lợi'")
    try:
        welfare_elements = await page.query_selector_all(WELFARE_SELECTOR)
        if not welfare_elements:
            print("CẢNH BÁO: Không tìm thấy danh sách phúc lợi.")
            return "N/A"
        benefits = [(' '.join((await el.inner_text()).split()).strip()) for el in welfare_elements]
        return ", ".join(filter(None, benefits))
    except Exception as e:
        print(f"LỖI khi trích xuất phúc lợi: {e}")
        return "N/A"

async def fetch_job_details_from_url(page: Page, job_url: str) -> dict:
    details = {"HanNop": "N/A", "PhucLoi": "N/A", "MoTaCongViec": "N/A", "YeuCauCongViec": "N/A"}
    try:
        print(f"Đang truy cập URL chi tiết: {job_url}")
        await page.goto(job_url, wait_until="domcontentloaded", timeout=60000)
        details["HanNop"] = await extract_deadline(page)
        details["PhucLoi"] = await extract_welfare_benefits(page)
        details["MoTaCongViec"] = await extract_generic_section(page, ["Mô Tả Công Việc", "Chi tiết công việc"])
        details["YeuCauCongViec"] = await extract_generic_section(page, ["Yêu Cầu Công Việc", "Yêu cầu ứng viên"])
    except Exception as e:
        print(f"LỖI NGHIÊM TRỌNG khi xử lý URL {job_url}: {e}")
    return details

# --- Hàm điều khiển chính ---
async def main_scraper(start_page: int, end_page: int):
    if end_page < start_page:
        print(f"Lỗi: Trang kết thúc ({end_page}) không được nhỏ hơn trang bắt đầu ({start_page}).")
        return pd.DataFrame()

    async with async_playwright() as p:
        browser = await p.chromium.launch(headless=True)
        context = await browser.new_context(user_agent="Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/110.0.0.0 Safari/537.36")
        page = await context.new_page()

        total_pages_to_scrape = end_page - start_page + 1
        print(f"--- GIAI ĐOẠN 1: Bắt đầu cào {total_pages_to_scrape} trang (từ trang {start_page} đến {end_page}) ---")

        # <<< CHỈNH SỬA CHÍNH: Thay thế `asyncio.gather` bằng vòng lặp `for` tuần tự >>>
        all_jobs_data = []
        for page_num in range(start_page, end_page + 1):
            page_data = await scrape_job_list_page(page, page_num)
            if page_data:
                all_jobs_data.extend(page_data)
            # Thêm một khoảng nghỉ nhỏ giữa các request để lịch sự hơn với server
            print("Nghỉ 1 giây trước khi sang trang mới...")
            await asyncio.sleep(1)

        if not all_jobs_data:
            print("\nKhông có dữ liệu. Dừng chương trình.")
            await browser.close()
            return pd.DataFrame()

        df = pd.DataFrame(all_jobs_data)
        print(f"\n--- GIAI ĐOẠN 1 HOÀN TẤT: Cào được {len(df)} công việc cơ bản. ---")

        print(f"\n--- GIAI ĐOẠN 2: Bắt đầu cào thông tin chi tiết cho {len(df)} công việc ---")
        deadlines, welfares, descriptions, requirements = [], [], [], []
        for _, row in tqdm(df.iterrows(), total=len(df), desc="Đang cào chi tiết"):
            job_url = row['URL']
            if pd.isna(job_url) or not job_url.startswith("http"):
                details = {"HanNop": "URL Lỗi", "PhucLoi": "URL Lỗi", "MoTaCongViec": "URL Lỗi", "YeuCauCongViec": "URL Lỗi"}
            else:
                details = await fetch_job_details_from_url(page, job_url)
                await asyncio.sleep(0.5)
            deadlines.append(details["HanNop"])
            welfares.append(details["PhucLoi"])
            descriptions.append(details["MoTaCongViec"])
            requirements.append(details["YeuCauCongViec"])

        df['HanNop'] = deadlines
        df['PhucLoi'] = welfares
        df['MoTaCongViec'] = descriptions
        df['YeuCauCongViec'] = requirements
        print("\n--- GIAI ĐOẠN 2 HOÀN TẤT ---")
        await browser.close()

        column_order = ['TieuDeCongViec', 'TenCongTy', 'DiaDiem', 'MucLuong', 'HanNop', 'PhucLoi', 'MoTaCongViec', 'YeuCauCongViec', 'URL']
        df = df[column_order]

        try:
            df.to_excel(OUTPUT_FILE, index=False, engine='openpyxl')
            print(f"\n✅ ĐÃ HOÀN TẤT! Dữ liệu đã được lưu vào file: {OUTPUT_FILE}")
        except Exception as e:
            print(f"Lỗi khi lưu file Excel: {e}")
            csv_output_file = OUTPUT_FILE.replace('.xlsx', '.csv')
            df.to_csv(csv_output_file, index=False, encoding='utf-8-sig')
            print(f"Dữ liệu đã được lưu vào file: {csv_output_file}")
        return df

# --- Chạy chương trình ---
final_df = await main_scraper(TRANG_BAT_DAU, TRANG_KET_THUC)

if 'final_df' in locals() and not final_df.empty:
    print("\nXem trước 5 dòng dữ liệu cuối cùng:")
    display(final_df.head())
else:
    print("\nKhông có dữ liệu để hiển thị.")

--- GIAI ĐOẠN 1: Bắt đầu cào 84 trang (từ trang 1 đến 84) ---
Đang cào danh sách từ trang: https://careerviet.vn/viec-lam/tat-ca-viec-lam-vi.html
Tìm thấy 50 mục công việc trên trang 1.
Nghỉ 1 giây trước khi sang trang mới...
Đang cào danh sách từ trang: https://careerviet.vn/viec-lam/tat-ca-viec-lam-trang-2-vi.html
Tìm thấy 50 mục công việc trên trang 2.


ERROR:asyncio:Future exception was never retrieved
future: <Future finished exception=TargetClosedError('Target page, context or browser has been closed')>
playwright._impl._errors.TargetClosedError: Target page, context or browser has been closed


Nghỉ 1 giây trước khi sang trang mới...
Đang cào danh sách từ trang: https://careerviet.vn/viec-lam/tat-ca-viec-lam-trang-3-vi.html
Tìm thấy 50 mục công việc trên trang 3.
Nghỉ 1 giây trước khi sang trang mới...
Đang cào danh sách từ trang: https://careerviet.vn/viec-lam/tat-ca-viec-lam-trang-4-vi.html
Tìm thấy 50 mục công việc trên trang 4.
Nghỉ 1 giây trước khi sang trang mới...
Đang cào danh sách từ trang: https://careerviet.vn/viec-lam/tat-ca-viec-lam-trang-5-vi.html
Tìm thấy 50 mục công việc trên trang 5.
Nghỉ 1 giây trước khi sang trang mới...
Đang cào danh sách từ trang: https://careerviet.vn/viec-lam/tat-ca-viec-lam-trang-6-vi.html
Tìm thấy 50 mục công việc trên trang 6.
Nghỉ 1 giây trước khi sang trang mới...
Đang cào danh sách từ trang: https://careerviet.vn/viec-lam/tat-ca-viec-lam-trang-7-vi.html
Tìm thấy 50 mục công việc trên trang 7.
Nghỉ 1 giây trước khi sang trang mới...
Đang cào danh sách từ trang: https://careerviet.vn/viec-lam/tat-ca-viec-lam-trang-8-vi.html
Tìm thấy

Đang cào chi tiết:   0%|          | 0/4200 [00:00<?, ?it/s]

Đang truy cập URL chi tiết: https://careerviet.vn/vi/tim-viec-lam/chuyen-vien-ho-tro-ky-thuat-o-to-thuong-mai.35C4A0D4.html
INFO: Đang tìm và trích xuất mục: 'Hạn nộp'
INFO: Đang tìm và trích xuất mục: 'Phúc lợi'
INFO: Đang tìm các mục: ['Mô Tả Công Việc', 'Chi tiết công việc']
INFO: Tìm thấy tiêu đề khớp: 'Mô Tả Công Việc'
INFO: Đang tìm các mục: ['Yêu Cầu Công Việc', 'Yêu cầu ứng viên']
INFO: Tìm thấy tiêu đề khớp: 'Yêu Cầu Công Việc'


...

Đang cào chi tiết: 100%|█████████▉| 4199/4200 [3:33:35<00:03,  3.57s/it]

Đang truy cập URL chi tiết: https://careerviet.vn/vi/tim-viec-lam/nhan-vien-kinh-doanh-thiet-bi-dien.35C42578.html
INFO: Đang tìm và trích xuất mục: 'Hạn nộp'
INFO: Đang tìm và trích xuất mục: 'Phúc lợi'
INFO: Đang tìm các mục: ['Mô Tả Công Việc', 'Chi tiết công việc']
INFO: Tìm thấy tiêu đề khớp: 'Mô Tả Công Việc'
INFO: Đang tìm các mục: ['Yêu Cầu Công Việc', 'Yêu cầu ứng viên']
INFO: Tìm thấy tiêu đề khớp: 'Yêu Cầu Công Việc'


Đang cào chi tiết: 100%|██████████| 4200/4200 [3:33:38<00:00,  3.05s/it]



--- GIAI ĐOẠN 2 HOÀN TẤT ---
Lỗi khi lưu file Excel: TẬP ĐOÀN HẠ TẦNG ĐÔ THỊ cannot be used in worksheets.
Dữ liệu đã được lưu vào file: careerviet_jobs_full_details_final.csv

Xem trước 5 dòng dữ liệu cuối cùng:


TieuDeCongViec  \
0  Chuyên Viên Hỗ Trợ Kỹ Thuật ( ô tô thương mại)...   
1                         CHUYÊN VIÊN PHỤ TÙNG (MỚI)   
2  PHÓ TRƯỞNG BỘ PHẬN PHÁP LÝ – ĐĂNG KIỂM XE CBU/...   
3                   Tài Xế Lái Xe Cho Giám Đốc (MỚI)   
4             Phiên dịch viên tiếng Trung Quốc (MỚI)   

                   TenCongTy      DiaDiem           MucLuong      HanNop  \
0  CÔNG TY CP TM DV AN SƯƠNG       Hà Nội         Cạnh tranh  31/10/2025   
1  CÔNG TY CP TM DV AN SƯƠNG  Hồ Chí Minh   8 Tr - 20 Tr VND  30/09/2025   
2  CÔNG TY CP TM DV AN SƯƠNG       Hà Nội         Cạnh tranh  31/08/2025   
3  CÔNG TY CP TM DV AN SƯƠNG  Hồ Chí Minh   8 Tr - 10 Tr VND  30/06/2025   
4  CÔNG TY CP TM DV AN SƯƠNG       Hà Nội  18 Tr - 25 Tr VND  31/08/2025   

                                             PhucLoi  \
0  Chế độ bảo hiểm, Du Lịch, Đồng phục, Chế độ th...   
1  Chế độ bảo hiểm, Du Lịch, Đồng phục, Chế độ th...   
2  Chế độ bảo hiểm, Du Lịch, Đồng phục, Chế độ th...   
3  Chế độ bảo hiểm, Du Lịch, Đồng phục, Chế độ th...   
4  Chế độ bảo hiểm, Du Lịch, Chế độ thưởng, Chăm ...   

                                        MoTaCongViec  \
0  • Hỗ trợ kỹ thuật & hướng dẫn sửa chữa cho hệ ...   
1  - Xây dựng chính sách, kế hoạch và KPI kinh do...   
2  Mô tả công việc: - Quản lý hồ sơ pháp lý – kỹ ...   
3  Mô tả công việc Phụ trách đưa đón, chuyên chở ...   
4  - Phiên dịch, biên dịch tài liệu kỹ thuật và n...   

                                      YeuCauCongViec  \
0  • Tốt nghiệp đại học ngành Cơ khí ô tô. • Tối ...   
1  -Tốt nghiệp ĐH ngành Cơ khí ô tô, Logistics, K...   
2  - Tốt nghiệp kỹ thuật ô tô, cơ khí, luật hoặc ...   
3  Nam, sức khỏe tốt, không bị cận; GPLX hạng B2 ...   
4  - Thành thạo tiếng Trung - Ưu tiên ứng viên có...   

                                                 URL  
0  https://careerviet.vn/vi/tim-viec-lam/chuyen-v...  
1  https://careerviet.vn/vi/tim-viec-lam/chuyen-v...  
2  https://careerviet.vn/vi/tim-viec-lam/pho-truo...  
3  https://careerviet.vn/vi/tim-viec-lam/tai-xe-l...  
4  https://careerviet.vn/vi/tim-viec-lam/phien-di...

In [ ]:
final_df

TieuDeCongViec  \
0     Chuyên Viên Hỗ Trợ Kỹ Thuật ( ô tô thương mại)...   
1                            CHUYÊN VIÊN PHỤ TÙNG (MỚI)   
2     PHÓ TRƯỞNG BỘ PHẬN PHÁP LÝ – ĐĂNG KIỂM XE CBU/...   
3                      Tài Xế Lái Xe Cho Giám Đốc (MỚI)   
4                Phiên dịch viên tiếng Trung Quốc (MỚI)   
...                                                 ...   
4195                       Nhân viên hành chính cấp cao   
4196                                  Tài Xế Xe công ty   
4197                                 Giám Đốc Tài Chính   
4198                       Chuyên viên phát triển dự án   
4199                 Nhân viên Kinh doanh thiết bị điện   

                                              TenCongTy      DiaDiem  \
0                             CÔNG TY CP TM DV AN SƯƠNG       Hà Nội   
1                             CÔNG TY CP TM DV AN SƯƠNG  Hồ Chí Minh   
2                             CÔNG TY CP TM DV AN SƯƠNG       Hà Nội   
3                             CÔNG TY CP TM DV AN SƯƠNG  Hồ Chí Minh   
4                             CÔNG TY CP TM DV AN SƯƠNG       Hà Nội   
...                                                 ...          ...   
4195                       Công ty TNHH Terumo Việt Nam       Hà Nội   
4196   Công ty TNHH Công Nghiệp Billion Ascent Việt Nam  Hồ Chí Minh   
4197        Công Ty CP XNK Hóa Chất & Thiết Bị Kim Ngưu       Hà Nội   
4198              CÔNG TY CỔ PHẦN ĐẦU TƯ INFINITY GROUP       Hà Nội   
4199  CÔNG TY CỔ PHẦN ĐẦU TƯ XÂY DỰNG VÀ CÔNG NGHỆ V...       Hà Nội   

               MucLuong      HanNop  \
0            Cạnh tranh  31/10/2025   
1      8 Tr - 20 Tr VND  30/09/2025   
2            Cạnh tranh  31/08/2025   
3      8 Tr - 10 Tr VND  30/06/2025   
4     18 Tr - 25 Tr VND  31/08/2025   
...                 ...         ...   
4195         Cạnh Tranh  04/07/2025   
4196   9 Tr - 10 Tr VND  04/07/2025   
4197         Cạnh Tranh  04/07/2025   
4198  18 Tr - 25 Tr VND  04/07/2025   
4199  10 Tr - 20 Tr VND  04/07/2025   

                                                PhucLoi  \
0     Chế độ bảo hiểm, Du Lịch, Đồng phục, Chế độ th...   
1     Chế độ bảo hiểm, Du Lịch, Đồng phục, Chế độ th...   
2     Chế độ bảo hiểm, Du Lịch, Đồng phục, Chế độ th...   
3     Chế độ bảo hiểm, Du Lịch, Đồng phục, Chế độ th...   
4     Chế độ bảo hiểm, Du Lịch, Chế độ thưởng, Chăm ...   
...                                                 ...   
4195  Chế độ bảo hiểm, Du Lịch, Phụ cấp, Xe đưa đón,...   
4196  Chế độ bảo hiểm, Du Lịch, Chế độ thưởng, Chăm ...   
4197  Laptop, Phụ cấp, Xe đưa đón, Du lịch nước ngoà...   
4198  Laptop, Chế độ bảo hiểm, Du Lịch, Phụ cấp, Đồn...   
4199  Chế độ bảo hiểm, Du Lịch, Chế độ thưởng, Chăm ...   

                                           MoTaCongViec  \
0     • Hỗ trợ kỹ thuật & hướng dẫn sửa chữa cho hệ ...   
1     - Xây dựng chính sách, kế hoạch và KPI kinh do...   
2     Mô tả công việc: - Quản lý hồ sơ pháp lý – kỹ ...   
3     Mô tả công việc Phụ trách đưa đón, chuyên chở ...   
4     - Phiên dịch, biên dịch tài liệu kỹ thuật và n...   
...                                                 ...   
4195  1 - Mô tả công việc: Quản lý các nhóm công việ...   
4196  Lái xe 4 chỗ/ 7 chỗ phục vụ nhu cầu di chuyển ...   
4197  Mục tiêu công việc: Chịu trách nhiệm cao nhất ...   
4198  Thực hiện các thủ tục pháp lý của dự án Theo d...   
4199  · Tư vấn lắp đặt hệ thống điện mặt trời cho hộ...   

                                         YeuCauCongViec  \
0     • Tốt nghiệp đại học ngành Cơ khí ô tô. • Tối ...   
1     -Tốt nghiệp ĐH ngành Cơ khí ô tô, Logistics, K...   
2     - Tốt nghiệp kỹ thuật ô tô, cơ khí, luật hoặc ...   
3     Nam, sức khỏe tốt, không bị cận; GPLX hạng B2 ...   
4     - Thành thạo tiếng Trung - Ưu tiên ứng viên có...   
...                                                 ...   
4195  - Bắt buộc tốt nghiệp Đại học, các chuyên ngàn...   
4196  Nam, từ 30 đến 45 tuổi, sức khỏe tốt. Có bằng ...   
4197  • Nam/Nữ từ 35 - 55 tuổi • Tốt nghiệp đại h